# Objectives {.unnumbered}

By the end of this lab, you will:
1. Load and analyze the **Lightcast dataset** in **Spark DataFrame**.
2. Create **five easy and three medium-complexity visualizations** using **Plotly**.
3. Explore **salary distributions, employment trends, and job postings**.
4. Analyze **skills in relation to NAICS/SOC/ONET codes and salaries**.
5. Customize **colors, fonts, and styles** in all visualizations (**default themes result in a 2.5-point deduction**).
6. Follow **best practices for reporting on data communication**.

# Step 1: Load the Dataset {.unnumbered}


In [15]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "vscode"
from pyspark.sql import SparkSession
from pyspark.sql.functions import col ,explode, split, from_json
import plotly.graph_objects as go
from pyspark.sql.types import ArrayType, StringType


# Initialize Spark Session
spark = SparkSession.builder.appName("LightcastData").getOrCreate()

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("./data/lightcast_job_postings.csv")

# Show Schema and Sample Data
df.printSchema()
df.show(5)


root
 |-- ID: string (nullable = true)
 |-- LAST_UPDATED_DATE: date (nullable = true)
 |-- LAST_UPDATED_TIMESTAMP: timestamp (nullable = true)
 |-- DUPLICATES: integer (nullable = true)
 |-- POSTED: date (nullable = true)
 |-- EXPIRED: date (nullable = true)
 |-- DURATION: integer (nullable = true)
 |-- SOURCE_TYPES: string (nullable = true)
 |-- SOURCES: string (nullable = true)
 |-- URL: string (nullable = true)
 |-- ACTIVE_URLS: string (nullable = true)
 |-- ACTIVE_SOURCES_INFO: string (nullable = true)
 |-- TITLE_RAW: string (nullable = true)
 |-- BODY: string (nullable = true)
 |-- MODELED_EXPIRED: date (nullable = true)
 |-- MODELED_DURATION: integer (nullable = true)
 |-- COMPANY: integer (nullable = true)
 |-- COMPANY_NAME: string (nullable = true)
 |-- COMPANY_RAW: string (nullable = true)
 |-- COMPANY_IS_STAFFING: boolean (nullable = true)
 |-- EDUCATION_LEVELS: string (nullable = true)
 |-- EDUCATION_LEVELS_NAME: string (nullable = true)
 |-- MIN_EDULEVELS: integer (nullable

# Salary Distribution by Employment Type
- Identify salary trends across different employment types.
- **Filter the dataset**
  - Remove records where **salary is missing or zero**.
- **Aggregate Data**
  - Group by **employment type** and compute salary distribution.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `EMPLOYMENT_TYPE_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize **colors, fonts, and styles** to avoid a **2.5-point deduction**.
- **Explanation:** Write two sentences about what the graph reveals.



In [2]:
# Your Code for 1st question here
pdf = df.select("EMPLOYMENT_TYPE_NAME", "SALARY").toPandas()
fig = px.box(pdf, x="EMPLOYMENT_TYPE_NAME", y="SALARY", title="Salary Distribution by Employment Type", color_discrete_sequence=["#636EFA"])
fig.update_layout(font_family="Arial", title_font_size=16)
fig.show()

Full time employees have higher medians, and the data has little variation meaning the full-time salary structure is stable.

# Salary Distribution by Industry
- Compare salary variations across industries.
- **Filter the dataset**
  - Keep records where **salary is greater than zero**.
- **Aggregate Data**
  - Group by **NAICS industry codes**.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `NAICS2_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize colors, fonts, and styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [3]:
df_q2 = df.filter(col("SALARY_FROM") > 0)
pdf_q2 = df_q2.select("NAICS2_NAME", "SALARY_FROM").toPandas()

fig = px.box(pdf_q2, x="NAICS2_NAME", y="SALARY_FROM",
             title="Salary Distribution by Industry",
             color_discrete_sequence=["#1f77b4"])
fig.update_layout(
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font_size=20,
    xaxis=dict(tickangle=45),
    yaxis_title="Salary (USD)",
    xaxis_title="Industry"
)

Technology-related industries tend to offer higher median salaries, driven by demand for skilled professionals.
Retail and service industries show lower, more uniform salaries, reflecting standardized wage structures.

# Job Posting Trends Over Time
- Analyze how job postings fluctuate over time.
- **Aggregate Data**
  - Count job postings per **posted date (`POSTED`)**.
- **Visualize results**
  - Create a **line chart** where:
    - **X-axis** = `POSTED`
    - **Y-axis** = `Number of Job Postings`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [5]:
df_q3 = df.groupBy("POSTED").count().orderBy("POSTED")
pdf_q3 = df_q3.toPandas()

fig = px.line(pdf_q3, x="POSTED", y="count",
              title="Job Posting Trends Over Time",
              line_shape="linear", color_discrete_sequence=["#ff7f0e"])
fig.update_layout(
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font_size=20,
    yaxis_title="Number of Postings",
    xaxis_title="Date"
)


Job postings exhibit seasonal peaks, often around hiring cycles like the early of the year or post-summer.

# Top 10 Job Titles by Count
- Identify the most frequently posted job titles.
- **Aggregate Data**
  - Count the occurrences of each **job title (`TITLE_NAME`)**.
  - Select the **top 10 most frequent titles**.
- **Visualize results**
  - Create a **bar chart** where:
    - **X-axis** = `TITLE_NAME`
    - **Y-axis** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [6]:
df_q4 = df.groupBy("TITLE_NAME").count().orderBy(col("count").desc()).limit(10)
pdf_q4 = df_q4.toPandas()

fig = px.bar(pdf_q4, x="TITLE_NAME", y="count",
             title="Top 10 Job Titles by Count",
             color_discrete_sequence=["#2ca02c"])
fig.update_layout(
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font_size=20,
    yaxis_title="Number of Postings",
    xaxis_title="Job Title",
    xaxis=dict(tickangle=45)
)

High-demand roles like Data Analyst dominate postings, reflecting tech sector growth. Analystic skills seems to be the most needed in the job market.

# Remote vs On-Site Job Postings
- Compare the proportion of remote and on-site job postings.
- **Aggregate Data**
  - Count job postings by **remote type (`REMOTE_TYPE_NAME`)**.
- **Visualize results**
  - Create a **pie chart** where:
    - **Labels** = `REMOTE_TYPE_NAME`
    - **Values** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [7]:
df_q5 = df.groupBy("REMOTE_TYPE_NAME").count()
pdf_q5 = df_q5.toPandas()

fig = px.pie(pdf_q5, names="REMOTE_TYPE_NAME", values="count",
             title="Remote vs On-Site Job Postings",
             color_discrete_sequence=px.colors.qualitative.Pastel)
fig.update_layout(
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font_size=20
)

Remote job postings are high, with the growing Hybrid Remote roles, it is reflecting shifts toward flexible work arrangements.

# Skill Demand Analysis by Industry (Stacked Bar Chart)
- Identify which skills are most in demand in various industries.
- **Aggregate Data**
  - Extract **skills** from job postings.
  - Count occurrences of skills grouped by **NAICS industry codes**.
- **Visualize results**
  - Create a **stacked bar chart** where:
    - **X-axis** = `Industry`
    - **Y-axis** = `Skill Count`
    - **Color** = `Skill`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [16]:
schema = ArrayType(StringType())
df_with_array = df.filter(col("SKILLS_NAME").isNotNull()) \
                  .withColumn("SKILLS_ARRAY", from_json(col("SKILLS_NAME"), schema))

In [28]:
df_exploded = df_with_array.filter(col("SKILLS_ARRAY").isNotNull()) \
                           .select("NAICS2", explode(col("SKILLS_ARRAY")).alias("SKILL"))
top_skills_df = df_exploded.groupBy("SKILL") \
                           .count() \
                           .orderBy(col("count").desc()) \
                           .limit(10)
top_skills = [row["SKILL"] for row in top_skills_df.collect()]
print("Top 10 Skills:", top_skills)

Top 10 Skills: ['Communication', 'Data Analysis', 'Management', 'SQL (Programming Language)', 'Problem Solving', 'Leadership', 'Computer Science', 'Operations', 'Project Management', 'Business Process']


In [29]:
df_filtered = df_exploded.filter(col("SKILL").isin(top_skills)) \
                         .filter(col("NAICS2").isNotNull())
df_q6 = df_filtered.groupBy("NAICS2", "SKILL") \
                   .count()
pdf_q6 = df_q6.toPandas()

In [30]:
fig = px.bar(pdf_q6, 
             x="NAICS2", 
             y="count", 
             color="SKILL", 
             title="Skill Demand by Industry (NAICS2)",
             labels={"NAICS2": "Industry", "count": "Skill Count", "SKILL": "Skill"},
             color_discrete_sequence=px.colors.qualitative.Bold)
fig.update_layout(
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font=dict(size=20, family="HelveticaNeue-CondensedBold"),
    xaxis_title="Industry",
    yaxis_title="Skill Count",
    xaxis=dict(tickangle=45),
    legend_title="Skills",
    barmode="stack"
)

Only top 10 skills are selected because there are too many values and the graph could not be created with all skills selected.
The stacked bar chart reveals that NAICS2 code "99" (likely a miscellaneous category) has a high demand for skills like "Problem Solving" and "Project Management," indicating a focus on tech and management roles.
Industries with codes like "54" (Professional, Scientific, and Technical Services) show significant demand for "Data Analysis" and "Technical Support," reflecting their reliance on analytical and IT skills.


# Salary Analysis by ONET Occupation Type (Bubble Chart)
- Analyze how salaries differ across ONET occupation types.
- **Aggregate Data**
  - Compute **median salary** for each occupation in the **ONET taxonomy**.
- **Visualize results**
  - Create a **bubble chart** where:
    - **X-axis** = `ONET_NAME`
    - **Y-axis** = `Median Salary`
    - **Size** = Number of job postings
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [35]:
unique_onet_names = df.select("ONET_NAME") \
                      .filter(col("ONET_NAME").isNotNull()) \
                      .distinct()
unique_onet_names.show(truncate=False)

+------------------------------+
|ONET_NAME                     |
+------------------------------+
|Business Intelligence Analysts|
+------------------------------+



In [36]:
df_q7 = df.filter(col("SALARY_FROM") > 0) \
          .groupBy("ONET_NAME") \
          .agg({"SALARY_FROM": "median", "*": "count"}) \
          .withColumnRenamed("median(SALARY_FROM)", "median_salary") \
          .withColumnRenamed("count(1)", "job_count")
pdf_q7 = df_q7.toPandas()

fig = px.scatter(pdf_q7, x="ONET_NAME", y="median_salary", size="job_count",
                 title="Salary by ONET Occupation",
                 color_discrete_sequence=["#d62728"])
fig.update_layout(
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font_size=20,
    yaxis_title="Median Salary (USD)",
    xaxis_title="ONET Occupation",
    xaxis=dict(tickangle=45)
)

There is only one item under ONET_NAME, so the median for Business Intelligence Analysts is 88k.

# Career Pathway Trends (Sankey Diagram)
- Visualize job transitions between different occupation levels.
- **Aggregate Data**
  - Identify career transitions between **SOC job classifications**.
- **Visualize results**
  - Create a **Sankey diagram** where:
    - **Source** = `SOC_2021_2_NAME`
    - **Target** = `SOC_2021_3_NAME`
    - **Value** = Number of transitions
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [25]:
df_q8 = df.groupBy("SOC_2021_2_NAME", "SOC_2021_3_NAME").count()
pdf_q8 = df_q8.toPandas()

labels = list(set(pdf_q8["SOC_2021_2_NAME"].tolist() + pdf_q8["SOC_2021_3_NAME"].tolist()))
source = [labels.index(x) for x in pdf_q8["SOC_2021_2_NAME"]]
target = [labels.index(x) for x in pdf_q8["SOC_2021_3_NAME"]]
value = pdf_q8["count"]

fig = go.Figure(data=[go.Sankey(
    node=dict(label=labels, color="#9467bd"),
    link=dict(source=source, target=target, value=value, color="#e377c2")
)])
fig.update_layout(
    title_text="Career Pathway Trends",
    font=dict(family="Helvetica Neue", size=16, color="#333"),
    title_font_size=20
)